**Dividend+ value Investing  Strategy**

- Dividend Yield > 2  
- Dividend 5 Year Average > 1%  
- EPS 5 Year Avg > 8%  
- Price to Book < 1.2  
- Sales 5 Year Avg > 3%  
- Payout Ratio < 60  
- P/E (This Year's Estimate) Less than or Equal to 25.0  
- EPS Growth (Proj This Quarter vs. Same Quarter Prior Yr) Highest 20% for industry (pred)  
- EPS Growth (Proj this Yr vs. Last Yr) Highest 20% for industry (pred)  

**Undervalued stock**
- Trailing P/E: 0 - 20  
- Price / Earnings to Growth (P/E/G): < 1, 1 yr.  
- % Change in EPS (Basic): 25% to 50% and 50% to 100% and > 100%  

In [354]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import requests
from datetime import datetime
import time

In [392]:
fh_key = 'bt3efpf48v6tfcs816eg'
fm_key = '8a1cf9d14d53126b05c8a7636fe3d006'

SP = requests.get(f'https://financialmodelingprep.com/api/v3/sp500_constituent?&apikey={fm_key}').json()    
SP = pd.DataFrame(SP)
sp = SP['symbol'].values.tolist()
NASDAQ = requests.get(f'https://financialmodelingprep.com/api/v3/nasdaq_constituent?&apikey={fm_key}').json()
NASDAQ = pd.DataFrame(NASDAQ)
nasdaq = NASDAQ['symbol'].values.tolist()
DJI = requests.get(f'https://financialmodelingprep.com/api/v3/dowjones_constituent?&apikey={fm_key}').json()
DJI = pd.DataFrame(DJI)
dji = DJI['symbol'].values.tolist()

tickers = sp + nasdaq + dji
tickers = np.array(tickers)
tickers = np.unique(tickers)

In [393]:
def paras(ticker):
    def tdf(data):
        return pd.DataFrame(data)

    # setup the dataframe
    # res = pd.DataFrame(columns = ['Date', 'symbol', 'dividendYield', 'DY_5avg', 'EPS_5avg', 'priceToBookRatio',\
    #                               'Sales_5avg', 'payoutRatio', 'EPSG_Q', 'EPSG_Y', 'PE_est',\
    #                               'priceEarningsRatio',  'Trailing_PE', 'priceEarningsToGrowthRatio', 'EPS_d'])
    res = pd.DataFrame(columns = ['Date', 'symbol', 'dividendYield', 'DY_5avg', 'EPS_5avg', 'priceToBookRatio',\
                                  'Sales_5avg', 'payoutRatio', 'PE_est',\
                                  'priceEarningsRatio',  'Trailing_PE', 'priceEarningsToGrowthRatio', 'EPS_d'])

    today = datetime.now().strftime("%d/%m/%Y %H:%M:%S")
    res = res.append({'Date': today}, ignore_index=True)
    res = res.set_index('Date')

    res.loc[today, 'symbol'] = ticker

    ratios = requests.get(f'https://financialmodelingprep.com/api/v3/ratios/{ticker}?limit=5&apikey={fm_key}').json()
    rs = ['dividendYield', 'priceToBookRatio', 'payoutRatio', 'priceEarningsRatio', 'priceEarningsToGrowthRatio']
    # eps = requests.get(f'https://financialmodelingprep.com/api/v3/income-statement-as-reported/{ticker}?limit=5&apikey={fm_key}').json()    
    # eps_temp = tdf(eps)
    # res.loc[today, 'EPS_5avg'] = np.mean(eps_temp.loc[:, 'earningspersharebasic'])
    is_growth = requests.get(f'https://financialmodelingprep.com/api/v3/income-statement-growth/{ticker}?apikey={fm_key}&limit=40').json()
    is_growth = tdf(is_growth)
    ttms = requests.get(f'https://financialmodelingprep.com/api/v3/ratios-ttm/{ticker}?apikey={fm_key}').json()
    
    fgrowth = requests.get(f'https://financialmodelingprep.com/api/v3/financial-growth/{ticker}?limit=2&apikey={fm_key}').json()
    # current price
    cp = requests.get(f'https://financialmodelingprep.com/api/v3/quote/{ticker}?apikey={fm_key}').json()[0]['price']

    if len(ratios) == 0:
        for i in rs:
            res.loc[today, i] = np.nan
        res.loc[today, 'DY_5avg'] = np.nan
    else:
        for i in rs:
            res.loc[today, i] = ratios[0][i]
    
        ratios_temp = pd.DataFrame(ratios)
        res.loc[today, 'DY_5avg'] = np.mean(ratios_temp.loc[:,'dividendYield'])

    res.loc[today, 'EPS_5avg'] = np.mean(is_growth.growthEPS[:5])

    res.loc[today, 'Sales_5avg'] = np.mean(is_growth.growthRevenue[:5])
    
    if len(ttms) == 1:
        ttms = tdf(ttms)
        res.loc[today, 'Trailing_PE'] = ttms.priceEarningsRatioTTM.item()
    else: 
        res.loc[today, 'Trailing_PE'] = np.nan
    
    res.loc[today, 'EPS_d'] = fgrowth[0]['epsgrowth']

    # res.loc[today, 'EPS_d'] = (eps_temp.loc[0, 'earningspersharebasic']\
    #                            - eps_temp.loc[1, 'earningspersharebasic'])/ eps_temp.loc[1, 'earningspersharebasic']

    eps_est = requests.get(f'https://finnhub.io/api/v1/stock/earnings?symbol={ticker}&token={fh_key}').json()
    est = eps_est[0]['estimate']
    if est is None:
        res.loc[today, 'PE_est'] = np.nan
    else:
        res.loc[today, 'PE_est'] = cp / eps_est[0]['estimate']

    return res

In [394]:
def dvscreener(ticker):
    ps = paras(ticker)
    ps = ps.fillna(value = np.nan)
    nn = sum(ps.isna().iloc[0,:])
    if (nn == 0) & (ps.dividendYield.item() > 0.02) & (ps.DY_5avg.item() > 0.01)\
    & (ps.EPS_5avg.item() > 0.08) & (ps.priceToBookRatio.item() < 1.2)\
    & (ps.Sales_5avg.item() > 0.03) & (ps.payoutRatio.item() < 0.6) & (ps.PE_est.item() <= 25.0):
        return True
    else:
        return False

def undervalue(ticker):
    ps = paras(ticker)
    ps = ps.fillna(value = np.nan)
    nn = sum(ps.isna().iloc[0,:])
    if (nn == 0) & (0 < ps.Trailing_PE.item() < 20) & (ps.priceEarningsToGrowthRatio.item() < 1)\
    & (0.25 < ps.EPS_d.item() < 0.5):
        return True
    else:
        return False

In [402]:
valid = []
n = 15
groups = np.array_split(tickers, n)
for group in groups:
    for ticker in group:
        if dvscreener(ticker):
            valid.append(ticker)
    time.sleep(60)

valid

['UNM']

In [403]:
undervalued = []
n = 15
groups = np.array_split(tickers, n)
for group in groups:
    for ticker in group:
        if undervalue(ticker):
            undervalued.append(ticker)
    time.sleep(60)

undervalued

['ADM',
 'AON',
 'DHI',
 'HII',
 'HUM',
 'IVZ',
 'K',
 'LEN',
 'MAS',
 'MS',
 'NOC',
 'ORCL',
 'PGR',
 'PHM',
 'PNC',
 'TROW']

# Draft

In [287]:
# def tdf(data):
#     return pd.DataFrame(data)

# # setup the dataframe
# # res = pd.DataFrame(columns = ['Date', 'symbol', 'dividendYield', 'DY_5avg', 'EPS_5avg', 'priceToBookRatio',\
# #                               'Sales_5avg', 'payoutRatio', 'EPSG_Q', 'EPSG_Y', 'PE_est',\
# #                               'priceEarningsRatio',  'Trailing_PE', 'priceEarningsToGrowthRatio', 'EPS_d'])
# res = pd.DataFrame(columns = ['Date', 'symbol', 'dividendYield', 'DY_5avg', 'EPS_5avg', 'priceToBookRatio',\
#                               'Sales_5avg', 'payoutRatio', 'PE_est',\
#                               'priceEarningsRatio',  'Trailing_PE', 'priceEarningsToGrowthRatio', 'EPS_d'])

# today = datetime.now().strftime("%d/%m/%Y %H:%M:%S")
# res = res.append({'Date': today}, ignore_index=True)
# res = res.set_index('Date')

# res.loc[today, 'symbol'] = ticker

# ratios = requests.get(f'https://financialmodelingprep.com/api/v3/ratios/{ticker}?limit=5&apikey={fm_key}').json()
# rs = ['dividendYield', 'priceToBookRatio', 'payoutRatio', 'priceEarningsRatio', 'priceEarningsToGrowthRatio']
# # eps = requests.get(f'https://financialmodelingprep.com/api/v3/income-statement-as-reported/{ticker}?limit=5&apikey={fm_key}').json()    
# # eps_temp = tdf(eps)
# # res.loc[today, 'EPS_5avg'] = np.mean(eps_temp.loc[:, 'earningspersharebasic'])
# is_growth = requests.get(f'https://financialmodelingprep.com/api/v3/income-statement-growth/{ticker}?apikey={fm_key}&limit=40').json()
# is_growth = tdf(is_growth)
# ttms = requests.get(f'https://financialmodelingprep.com/api/v3/ratios-ttm/{ticker}?apikey={fm_key}').json()
# ttms = tdf(ttms)
# fgrowth = requests.get(f'https://financialmodelingprep.com/api/v3/financial-growth/{ticker}?limit=2&apikey={fm_key}').json()
# # current price
# cp = requests.get(f'https://financialmodelingprep.com/api/v3/quote/{ticker}?apikey={fm_key}').json()[0]['price']

# for i in rs:
#     res.loc[today, i] = ratios[0][i]
# ratios_temp = pd.DataFrame(ratios)

# res.loc[today, 'DY_5avg'] = np.mean(ratios_temp.loc[:,'dividendYield'])

# res.loc[today, 'EPS_5avg'] = np.mean(is_growth.growthEPS[:5])

# res.loc[today, 'Sales_5avg'] = np.mean(is_growth.growthRevenue[:5])

# res.loc[today, 'Trailing_PE'] = ttms.priceEarningsRatioTTM.item()

# res.loc[today, 'EPS_d'] = fgrowth[0]['epsgrowth']

# # res.loc[today, 'EPS_d'] = (eps_temp.loc[0, 'earningspersharebasic']\
# #                            - eps_temp.loc[1, 'earningspersharebasic'])/ eps_temp.loc[1, 'earningspersharebasic']

# eps_est = requests.get(f'https://finnhub.io/api/v1/stock/earnings?symbol={ticker}&token={fh_key}').json()
# res.loc[today, 'PE_est'] = cp / eps_est[0]['estimate']

# res

In [288]:
# eps = requests.get(f'https://financialmodelingprep.com/api/v3/income-statement-as-reported/{ticker}?limit=5&apikey={fm_key}').json()
# eps = pd.DataFrame(eps)
# eps.loc[:,['date', 'earningspersharebasic']]

In [289]:
# fgrowth = requests.get(f'https://financialmodelingprep.com/api/v3/financial-growth/{ticker}?limit=5&apikey={fm_key}').json()
# # fgrowth[0]['epsgrowth']
# fgrowth = pd.DataFrame(fgrowth)
# fgrowth.loc[:,['date', 'epsgrowth']]

In [290]:
# # r = requests.get(f'https://finnhub.io/api/v1/stock/financials-reported?symbol={ticker}&token={fh_key}').json()
# # pd.DataFrame(r['data'][1]['report']['ic'])
# eps.earningspersharebasic.pct_change(-1)